# Analysis 2
This analysis was edited from the *opynfield* tutorial. Here, we are comparing two groups of Canton-S flies that were run in different sized arenas. We expect that flies in the larger arenas will explore more as a function of time, but the same as a function of coverage.

## 1. Import the package and needed functions / classes

In [1]:
from opynfield.config.user_input import UserInput
from opynfield.config.defaults_settings import Defaults
from opynfield.config.cov_asymptote import CoverageAsymptote
from opynfield.config.model_settings import set_up_fits
from opynfield.config.plot_settings import PlotSettings
from opynfield.readin.run_all import run_all_track_types
from opynfield.calculate_measures.calculate_measures import tracks_to_measures
from opynfield.summarize_measures.summarize_individuals import individual_measures_to_dfs
from opynfield.summarize_measures.summarize_groups import all_group_averages
from opynfield.fit_models.fit_individual_models import fit_all, find_fit_bounds, re_fit_all
from opynfield.fit_models.fit_group_models import group_fit_all
from opynfield.stat_test.stat_test import format_params, format_group_params, run_tests
from opynfield.plotting.plot_individuals import plot_all_individuals, plot_traces
from opynfield.plotting.plot_solo_groups import plot_all_solo_groups
from opynfield.plotting.plot_solo_groups_with_individuals import plot_components_of_solo_groups
from opynfield.plotting.plot_group_comparisons import plot_all_group_comparisons
from opynfield.readin.summary_file import summary_file

from copy import deepcopy

## 2. Define the settings to use

### 2a. Set up your user inputs
The data we have for these groups is in text file format. They were originally recorded (and smoothed) in Ethovision, before the raw coordinates were extracted using a MATLAB Program. Since arena size is defined at the UserInput level, we will create two sets of parameters to read in the groups separately, and combine them later.

For the first group, in 5.0cm diameter arenas, we set the name, filetype, arena radius, and edge distance. We set the edge distance to 2.5/4.2 so that the edge region takes up proportionally the same amount of the arena radisu as the 1cm edge region does in the 4.2cm radius arena. All other settings are kept the same as in Analysis 1.

For the second group, in the standard 8.4cm diameter arenas, we set the name and filetype. All other settings are kept the same as in Analysis 1.

user_settings1 and user_settings2 will be used to read in the files and calculate behavioral measures. Later, we will need a unified set, user_settings, that includes both groups in order to loop through the groups for plotting and other analyses.

In [2]:
user_settings1 = UserInput(groups_and_types = {"5.0": ["Ethovision Through MATLAB"]},
                          groups_to_paths = {"5.0": "5.0"},
                          arena_radius_cm = 2.5,
                          sample_freq = 30,
                          edge_dist_cm = 2.5/4.2,
                          time_bin_size = 1,
                          inactivity_threshold = 0.001,
                          verbose = True,
                          result_path = '/Users/ellenmcmullen/Documents/GitHub/opynfield/test_data/2_ArenaSizeComparison/ExpectedResults')
user_settings2 = UserInput(groups_and_types = {"8.4": ["Ethovision Through MATLAB"]},
                          groups_to_paths = {"8.4": "8.4"},
                          arena_radius_cm = 4.2,
                          sample_freq = 30,
                          edge_dist_cm = 1,
                          time_bin_size = 1,
                          inactivity_threshold = 0.001,
                          verbose = True,
                          result_path = '/Users/ellenmcmullen/Documents/GitHub/opynfield/test_data/2_ArenaSizeComparison/ExpectedResults')
user_settings = UserInput(groups_and_types = {"5.0": ["Ethovision Through MATLAB"], "8.4": ["Ethovision Through MATLAB"]},
                          groups_to_paths = {"5.0": "5.0", "8.4": "8.4"},
                          arena_radius_cm = 9999, #should be obvious if this is propogated somewhere
                          sample_freq = 30,
                          edge_dist_cm = 1,
                          time_bin_size = 1,
                          inactivity_threshold = 0.001,
                          verbose = True,
                          result_path = '/Users/ellenmcmullen/Documents/GitHub/opynfield/test_data/2_ArenaSizeComparison/ExpectedResults')

### 2b. Prep the results directory

In [3]:
user_settings.prep_directory()

### 2c. Set up the default settings

In [4]:
default_settings = Defaults()

### 2d. Set up the coverage asymptote settings

In [5]:
asymptote_settings = CoverageAsymptote()

### 2e. Set up the model settings

In [6]:
model_settings = set_up_fits()

Sometimes the models fail to converge on the first attempt. You can go back to the model settings and update the max_eval parameter for the relationships that are causing problems like this:

In [7]:
for key in model_settings['pgca']:
    model_settings['pgca'][key].model.max_eval = 5000
    model_settings['pica'][key].model.max_eval = 5000
    model_settings['percent_coverage'][key].model.max_eval = 5000

### 2f. Set up the plotting settings

In [8]:
plot_settings = PlotSettings(group_colors={'5.0': 'b', '8.4': 'r'},
                             display_individual_figures=True,
                             display_solo_group_figures=True)

## 3. Read in your data
Here, we need to read in the two groups separately, so that we can apply their specific user_settings to them. Then we combine the list of tracks.

In [9]:
track_list1 = run_all_track_types(groups_and_types=user_settings1.groups_and_types,
                                 verbose=user_settings1.verbose,
                                 arena_radius_cm=user_settings1.arena_radius_cm,
                                 running_window_length=user_settings1.running_window_length,
                                 window_step_size=user_settings1.window_step_size,
                                 sample_freq=user_settings1.sample_freq,
                                 time_bin_size=user_settings1.time_bin_size,
                                 trim=user_settings1.trim)
track_list2 = run_all_track_types(groups_and_types=user_settings2.groups_and_types,
                                 verbose=user_settings2.verbose,
                                 arena_radius_cm=user_settings2.arena_radius_cm,
                                 running_window_length=user_settings2.running_window_length,
                                 window_step_size=user_settings2.window_step_size,
                                 sample_freq=user_settings2.sample_freq,
                                 time_bin_size=user_settings2.time_bin_size,
                                 trim=user_settings2.trim)
track_list = track_list1 + track_list2

['Ethovision Through MATLAB']
{'Ethovision Through MATLAB': ['5.0']}
Read In Ethovision Through MATLAB Files For Groups ['5.0']
Running Ethovision ML Tracker Files For Group: 5.0
5.0, File1 Out Of 136
Etho ML Track Converted To Numeric
Etho ML Track Subsampled
Etho ML Track Missing Values Filled
Combined Coordinate Center Point Calculated
Etho ML Track Centered
5.0, File2 Out Of 136
Etho ML Track Converted To Numeric
Etho ML Track Subsampled
Etho ML Track Missing Values Filled
Combined Coordinate Center Point Calculated
Etho ML Track Centered
5.0, File3 Out Of 136
Etho ML Track Converted To Numeric
Etho ML Track Subsampled
Etho ML Track Missing Values Filled
Combined Coordinate Center Point Calculated
Etho ML Track Centered
5.0, File4 Out Of 136
Etho ML Track Converted To Numeric
Etho ML Track Subsampled
Etho ML Track Missing Values Filled
Combined Coordinate Center Point Calculated
Etho ML Track Centered
5.0, File5 Out Of 136
Etho ML Track Converted To Numeric
Etho ML Track Subsampled

Just checking that we got all of the files!

In [10]:
len(track_list)

411

## 4. Calculate behavioral measures

### 4a. Generate the measures
Now we convert the two groups to standard tracks separately, and then combine the resultant lists. We also set the tracks_by_groups dictionary up with the group labels.

In [11]:
standard_track_list1, tracks_by_groups1 = tracks_to_measures(all_tracks=track_list1,
                                                           user_config=user_settings1,
                                                           default_settings=default_settings,
                                                           coverage_settings=asymptote_settings)
standard_track_list2, tracks_by_groups2 = tracks_to_measures(all_tracks=track_list2,
                                                           user_config=user_settings2,
                                                           default_settings=default_settings,
                                                           coverage_settings=asymptote_settings)
standard_track_list = standard_track_list1 + standard_track_list2
tracks_by_groups = {"5.0": standard_track_list1, "8.4": standard_track_list2}

Polar Coordinates Calculated
Activity Calculated
Turning Angles Calculated
Motion Probabilities Calculated
Coverage Bins Located
Coverage Calculated
Percent Coverage Calculated
PICA Calculated
Polar Coordinates Calculated
Activity Calculated
Turning Angles Calculated
Motion Probabilities Calculated
Coverage Bins Located
Coverage Calculated
Percent Coverage Calculated
PICA Calculated
Polar Coordinates Calculated
Activity Calculated
Turning Angles Calculated
Motion Probabilities Calculated
Coverage Bins Located
Coverage Calculated
Percent Coverage Calculated
PICA Calculated
Polar Coordinates Calculated
Activity Calculated
Turning Angles Calculated
Motion Probabilities Calculated
Coverage Bins Located
Coverage Calculated
Percent Coverage Calculated
PICA Calculated
Polar Coordinates Calculated
Activity Calculated
Turning Angles Calculated
Motion Probabilities Calculated
Coverage Bins Located
Coverage Calculated
Percent Coverage Calculated
PICA Calculated
Polar Coordinates Calculated
Activi

/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/calculate_measures/calculate_measures.py:286: RuntimeWarning: invalid value encountered in divide
  perc_cov = cov / highest_cov
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/calculate_measures/calculate_measures.py:286: RuntimeWarning: invalid value encountered in divide
  perc_cov = cov / highest_cov


Coverage Bins Located
Coverage Calculated
Percent Coverage Calculated
PICA Calculated
Polar Coordinates Calculated
Activity Calculated
Turning Angles Calculated
Motion Probabilities Calculated
Coverage Bins Located
Coverage Calculated
Percent Coverage Calculated
PICA Calculated
Polar Coordinates Calculated
Activity Calculated
Turning Angles Calculated
Motion Probabilities Calculated
Coverage Bins Located
Coverage Calculated
Percent Coverage Calculated
PICA Calculated
Polar Coordinates Calculated
Activity Calculated
Turning Angles Calculated
Motion Probabilities Calculated
Coverage Bins Located
Coverage Calculated
Percent Coverage Calculated
PICA Calculated
Polar Coordinates Calculated
Activity Calculated
Turning Angles Calculated
Motion Probabilities Calculated
Coverage Bins Located
Coverage Calculated
Percent Coverage Calculated
PICA Calculated
Polar Coordinates Calculated
Activity Calculated
Turning Angles Calculated
Motion Probabilities Calculated
Coverage Bins Located
Coverage Calc

/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/calculate_measures/calculate_measures.py:286: RuntimeWarning: invalid value encountered in divide
  perc_cov = cov / highest_cov


PICA Calculated
Polar Coordinates Calculated
Activity Calculated
Turning Angles Calculated
Motion Probabilities Calculated
Coverage Bins Located
Coverage Calculated
Percent Coverage Calculated
PICA Calculated
Polar Coordinates Calculated
Activity Calculated
Turning Angles Calculated
Motion Probabilities Calculated
Coverage Bins Located
Coverage Calculated
Percent Coverage Calculated
PICA Calculated
Polar Coordinates Calculated
Activity Calculated
Turning Angles Calculated
Motion Probabilities Calculated
Coverage Bins Located
Coverage Calculated
Percent Coverage Calculated
PICA Calculated
Polar Coordinates Calculated
Activity Calculated
Turning Angles Calculated
Motion Probabilities Calculated
Coverage Bins Located
Coverage Calculated
Percent Coverage Calculated
PICA Calculated
Polar Coordinates Calculated
Activity Calculated
Turning Angles Calculated
Motion Probabilities Calculated
Coverage Bins Located
Coverage Calculated
Percent Coverage Calculated
PICA Calculated
Polar Coordinates C

### 4b. Save the measures

In [12]:
individual_dfs = individual_measures_to_dfs(tracks_by_groups=tracks_by_groups,
                                            defaults=default_settings,
                                            user_inputs=user_settings)

Summarizing Tracks From Group 5.0
Summarizing Tracks From Group 8.4


### 4c. Calculate group averages of the measures

In [13]:
group_averages = all_group_averages(individual_measures_dfs=individual_dfs,
                                    test_defaults=default_settings,
                                    user_config=user_settings)

Averaging Tracks From Group 5.0 by time
Averaging Tracks From Group 8.4 by time
Averaging Tracks From Group 5.0 By coverage
Averaging Tracks From Group 8.4 By coverage
Averaging Tracks From Group 5.0 By pica
Averaging Tracks From Group 8.4 By pica
Averaging Tracks From Group 5.0 By pgca
Averaging Tracks From Group 8.4 By pgca
Averaging Tracks From Group 5.0 by percent coverage
Averaging Tracks From Group 8.4 by percent coverage


## 5. Fit models to individuals' measures

### 5a. Naive bounds

In [14]:
naive_fits = fit_all(individual_measures_dfs=individual_dfs,
                     defaults=default_settings,
                     model_params=model_settings)

Fitting Models To Tracks From Group 5.0 by time
Fitting Models To Tracks From Group 5.0 by coverage
Fitting Models To Tracks From Group 5.0 by pica
Fitting Models To Tracks From Group 5.0 by pgca
Fitting Models To Tracks From Group 5.0 by percent_coverage
Fitting Models To Tracks From Group 8.4 by time
Fitting Models To Tracks From Group 8.4 by coverage
Fitting Models To Tracks From Group 8.4 by pica
Fitting Models To Tracks From Group 8.4 by pgca
Fitting Models To Tracks From Group 8.4 by percent_coverage


### 5b. Find new bounds

In [15]:
upper_bounds, lower_bounds, p0s = find_fit_bounds(fits=naive_fits,
                                                  user_inputs=user_settings)

### 5c. Re-fit models

In [16]:
bounded_fits = re_fit_all(individual_measures_dfs=individual_dfs,
                          defaults=default_settings,
                          model_params=model_settings,
                          upper=upper_bounds,
                          lower=lower_bounds,
                          initial=p0s )

Re-Fitting Models To Tracks From Group 5.0 by time
Re-Fitting Models To Tracks From Group 5.0 by coverage
Re-Fitting Models To Tracks From Group 5.0 by pica
Re-Fitting Models To Tracks From Group 5.0 by pgca
Re-Fitting Models To Tracks From Group 5.0 by percent_coverage
Re-Fitting Models To Tracks From Group 8.4 by time
Re-Fitting Models To Tracks From Group 8.4 by coverage
Re-Fitting Models To Tracks From Group 8.4 by pica
Re-Fitting Models To Tracks From Group 8.4 by pgca
Re-Fitting Models To Tracks From Group 8.4 by percent_coverage


### 5d. Format and save the bounded individual fits

In [17]:
formatted_bounded_fits = format_params(bounded_fits=deepcopy(bounded_fits),
                                       defaults=default_settings,
                                       user_inputs=user_settings)

## 6. Fit models to group measures

### 6a. Fit the group models with bounds

In [18]:
group_fits = group_fit_all(individual_measures_dfs=individual_dfs,
                           defaults=default_settings,
                           model_params=model_settings,
                           upper=upper_bounds,
                           lower=lower_bounds,
                           initial=p0s)

Fitting Models To Entire Group 5.0 by time
Fitting Models To Entire Group 5.0 by coverage
Fitting Models To Entire Group 5.0 by pica
Fitting Models To Entire Group 5.0 by pgca
Fitting Models To Entire Group 5.0 by percent_coverage
Fitting Models To Entire Group 8.4 by time
Fitting Models To Entire Group 8.4 by coverage
Fitting Models To Entire Group 8.4 by pica
Fitting Models To Entire Group 8.4 by pgca
Fitting Models To Entire Group 8.4 by percent_coverage


### 6b. Format and save the bounded group fits

In [19]:
format_group_params(group_fits=deepcopy(group_fits),
                    defaults=default_settings,
                    user_inputs=user_settings)

## 7. Run statistical tests

In [20]:
run_tests(formatted_bounded_fits=formatted_bounded_fits,
          defaults=default_settings,
          user_inputs=user_settings)

## 8. Plot the results

### 8a. Plot individuals

In [21]:
plot_all_individuals(measures=individual_dfs,
                     model_params=bounded_fits,
                     model_info=model_settings,
                     defaults=default_settings,
                     plot_settings=plot_settings,
                     user_config=user_settings)

Plotting Individuals From Group 5.0 by time


/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:104: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:104: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:104: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:104: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:104: UserWarning: Figu

Plotting Individuals From Group 5.0 by coverage


/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: Figu

Plotting Individuals From Group 5.0 by pica


...

/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: Figu

Plotting Individuals From Group 8.4 by pgca


/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: Figu

Plotting Individuals From Group 8.4 by percent_coverage


/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:229: UserWarning: Figu

### 8b. Plot traces

In [22]:
plot_traces(tracks_by_groups=tracks_by_groups,
            plot_settings=plot_settings,
            user_input=user_settings)

/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_individuals.py:443: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()


### 8c. Plot group averages

In [23]:
plot_all_solo_groups(group_averages=group_averages,
                     group_fits=group_fits,
                     model_params=model_settings,
                     test_defaults=default_settings,
                     plot_settings=plot_settings,
                     user_config=user_settings)

Plotting Group 5.0 by time


/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_solo_groups.py:153: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_solo_groups.py:153: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_solo_groups.py:153: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_solo_groups.py:153: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_solo_groups.py:153: UserWarning: Figu

Plotting Group 5.0 by coverage


/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_solo_groups.py:297: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()


Plotting Group 5.0 by pica
Plotting Group 5.0 by pgca
Plotting Group 5.0 by percent_coverage
Plotting Group 8.4 by time


/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_solo_groups.py:153: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_solo_groups.py:153: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_solo_groups.py:153: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_solo_groups.py:153: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()
/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_solo_groups.py:153: UserWarning: Figu

Plotting Group 8.4 by coverage


/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_solo_groups.py:297: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()


Plotting Group 8.4 by pica
Plotting Group 8.4 by pgca
Plotting Group 8.4 by percent_coverage


### 8d. Plot group averages with component individuals

In [24]:
plot_components_of_solo_groups(individuals=individual_dfs,
                               individual_fits=bounded_fits,
                               groups=group_averages,
                               group_fits=group_fits,
                               model_specs=model_settings,
                               defaults=default_settings,
                               plot_settings=plot_settings,
                               user_inputs=user_settings)

Plotting Group And Individuals of 5.0 by time


/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_solo_groups_with_individuals.py:267: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()


Plotting Group And Individuals of 5.0 by coverage


/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_solo_groups_with_individuals.py:149: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()


Plotting Group And Individuals of 5.0 by pica
Plotting Group And Individuals of 5.0 by pgca
Plotting Group And Individuals of 5.0 by percent_coverage
Plotting Group And Individuals of 8.4 by time
Plotting Group And Individuals of 8.4 by coverage
Plotting Group And Individuals of 8.4 by pica
Plotting Group And Individuals of 8.4 by pgca
Plotting Group And Individuals of 8.4 by percent_coverage


### 8e. Plot group average comparisons

In [25]:
plot_all_group_comparisons(group_averages=group_averages,
                           group_fits=group_fits,
                           model_params=model_settings,
                           test_defaults=default_settings,
                           plot_settings=plot_settings,
                           user_config=user_settings)

Plotting Group Comparisons by time


/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_group_comparisons.py:142: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()


Plotting Group Comparisons by coverage


/Users/ellenmcmullen/opt/anaconda3/envs/opynfield_run/lib/python3.11/site-packages/opynfield/plotting/plot_group_comparisons.py:255: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  fig.show()


Plotting Group Comparisons by pica
Plotting Group Comparisons by pgca
Plotting Group Comparisons by percent_coverage


## 9. Summarize the run
Here I will run it with all 3 sets of user_settings. There will be some repeated information, but this will make it clear we ran the two groups separately and then combined them!

In [26]:
summary_file(tracks_by_group=tracks_by_groups,
             test_cov_asymptote=asymptote_settings,
             user_defaults=default_settings,
             model_settings=model_settings,
             plot_settings=plot_settings,
             user_config=user_settings1)
summary_file(tracks_by_group=tracks_by_groups,
             test_cov_asymptote=asymptote_settings,
             user_defaults=default_settings,
             model_settings=model_settings,
             plot_settings=plot_settings,
             user_config=user_settings2)
summary_file(tracks_by_group=tracks_by_groups,
             test_cov_asymptote=asymptote_settings,
             user_defaults=default_settings,
             model_settings=model_settings,
             plot_settings=plot_settings,
             user_config=user_settings)

Formatting Summary File
Formatting Summary File
Formatting Summary File


## You're done!